In [ ]:
# update the last value in "done" to True for all episodes.





In [20]:

import itertools
import h5py
import pathlib

import numpy as np

import torch

from torch.utils.data import Dataset, TensorDataset, ConcatDataset, DataLoader
from pytorch_lightning import LightningDataModule

import os
import json
import glob

from kaggle.api.kaggle_api_extended import KaggleApi
import gymu

WORLD_OF_BUGS_DATASET_KAGGLE = "benedictwilkinsai/world-of-bugs"
def prepare_data(path=".", force=False):
    api = KaggleApi()
    api.authenticate() # requires ~/.kaggle/kaggle.json file
    api.dataset_download_files(WORLD_OF_BUGS_DATASET_KAGGLE, quiet=False, unzip=True, force=force, path=str(path))
    # decompress dataset...? 

    # read files in path
    path = str(path) + "/**/*.hdf5" 
    print(f"DECOMPRESSING FILES...")
    for file in glob.glob(path, recursive=True):
        if force or pathlib.Path(file).exists():
            print(file)
            episodes, f = gymu.data.read_episodes(file, lazy=True, show_progress=False)
            gymu.data.write_episodes(file.replace("-compressed", ""), episodes, compression=None, show_progress=True)
            f.close()
prepare_data()

     

#def _get_data(ep):
#    print(ep['done'][-10:])

#with h5py.File("./NORMAL-50k-compressed.hdf5", "r") as f:
#    episodes = [_get_data(f[ep_name]) for ep_name in sorted(f.keys())]



world-of-bugs.zip: Skipping, found more recently modified local copy (use --force to force download)
DECOMPRESSING FILES...
./NORMAL-50k-compressed.hdf5


Writing episodes::   0%|          | 0/10 [00:00<?, ?it/s]

./NORMAL-300k-compressed.hdf5


Writing episodes::   0%|          | 0/60 [00:00<?, ?it/s]

./TEST/BlackScreen-compressed.hdf5


...

Writing episodes::   0%|          | 0/10 [00:00<?, ?it/s]

./TEST/TextureMissing-compressed.hdf5


Writing episodes::   0%|          | 0/10 [00:00<?, ?it/s]

./TEST/BoundaryHole-compressed.hdf5


Writing episodes::   0%|          | 0/29 [00:00<?, ?it/s]

In [42]:
## convert hdf5 file to tar archive....

import pathlib
import h5py
import glob
from pprint import pprint
from tqdm.auto import tqdm

from gymu.data import write_episode

import ray
ray.init()

def iterator(group):
    keys = [k.replace("observation", "state") for k in group.keys()]
    #dict of lists to list of dicts
    group = {k:v for k,v in group.items()}
    group['done'] = group['done'][...]
    group['done'][-1] = 1
    
    d = zip(*[x for x in group.values()])
    def _process(x):
        z = dict(zip(keys, x))
        if "bugmask" in z:
            z['info'] = (z['info'], z['bugmask'])
            del z['bugmask']
        return z
    for x in d:
        yield _process(x)
        
@ray.remote
def process(path):
    path = pathlib.Path(path)
    with h5py.File(str(path), "r") as f:
        for ep in f.keys():
            print(f"SAVING EP, {ep}, {path.stem}") 
            write_episode(iterator(f[ep]), path=f"./{path.stem}/{ep}")

for file in tqdm([f for f in glob.glob("./**/*.hdf5", recursive=True) if "compressed" not in f]):
    process.remote(file)

  0%|          | 0/12 [00:00<?, ?it/s]

0it [00:00, ?it/s]/home/ben/anaconda3/envs/PhD/lib/python3.8/site-packages/numpy/lib/npyio.py:713: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
(process pid=9519)   val = np.asanyarray(val)
0it [00:00, ?it/s]/home/ben/anaconda3/envs/PhD/lib/python3.8/site-packages/numpy/lib/npyio.py:713: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
(process pid=9521)   val = np.asanyarray(val)
0it [00:00, ?it/s]/home/ben/anaconda3/envs/PhD/lib/python3.8/site-packages/numpy/lib/npyio.py:713: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (wh

(process pid=9518) SAVING EP, ep-0000, ZClipping
(process pid=9519) SAVING EP, ep-0000, TextureCorruption
(process pid=9521) SAVING EP, ep-0000, BlackScreen
(process pid=9520) SAVING EP, ep-0000, GeometryCorruption
(process pid=9517) SAVING EP, ep-0000, GeometryClipping
(process pid=9516) SAVING EP, ep-0000, ZFighting
(process pid=9524) SAVING EP, ep-0000, CameraClipping
(process pid=9525) SAVING EP, ep-0000, BoundaryHole
(process pid=9522) SAVING EP, ep-0000, TextureMissing
(process pid=9527) SAVING EP, ep-0000, NORMAL-300k
(process pid=9526) SAVING EP, ep-0000, NORMAL-50k
(process pid=9523) SAVING EP, ep-0000, ScreenTear


26it [00:00, 125.25it/s]19) 
38it [00:00, 183.18it/s]21) 
23it [00:00, 112.35it/s]18) 
28it [00:00, 137.68it/s]20) 
32it [00:00, 154.00it/s]17) 
27it [00:00, 130.99it/s]16) 
31it [00:00, 148.34it/s]26) 
31it [00:00, 154.13it/s]27) 
34it [00:00, 160.45it/s]22) 
26it [00:00, 128.54it/s]24) 
40it [00:00, 202.98it/s]25) 
27it [00:00, 130.81it/s]23) 
39it [00:00, 117.03it/s]19) 
57it [00:00, 182.34it/s]21) 
35it [00:00, 114.85it/s]18) 
42it [00:00, 130.62it/s]20) 
48it [00:00, 155.48it/s]17) 
42it [00:00, 136.79it/s]16) 
49it [00:00, 160.74it/s]26) 
48it [00:00, 159.64it/s]27) 
51it [00:00, 151.76it/s]22) 
40it [00:00, 130.42it/s]24) 
68it [00:00, 236.74it/s]25) 
42it [00:00, 138.49it/s]23) 
52it [00:00, 119.92it/s]19) 
78it [00:00, 191.78it/s]21) 
48it [00:00, 118.54it/s]18) 
56it [00:00, 129.52it/s]20) 
65it [00:00, 158.25it/s]17) 
56it [00:00, 132.48it/s]16) 
66it [00:00, 163.61it/s]26) 
65it [00:00, 160.06it/s]27) 
67it [00:00, 151.46it/s]22) 
56it [00:00, 138.15it/s]24) 
89it [00:00, 2

(process pid=9525) SAVING EP, ep-0001, BoundaryHole


...

20it [00:00, 191.06it/s]27) 
43it [00:00, 211.44it/s]27) 
65it [00:00, 198.26it/s]27) 
85it [00:00, 193.63it/s]27) 
105it [00:00, 190.43it/s]7) 
126it [00:00, 193.82it/s]7) 
147it [00:00, 196.09it/s]7) 
167it [00:00, 195.80it/s]7) 
188it [00:00, 198.75it/s]7) 
210it [00:01, 204.31it/s]7) 
233it [00:01, 210.76it/s]7) 
256it [00:01, 214.19it/s]7) 
278it [00:01, 210.76it/s]7) 
300it [00:01, 201.82it/s]7) 
321it [00:01, 199.44it/s]7) 
342it [00:01, 200.75it/s]7) 
363it [00:01, 201.68it/s]7) 
384it [00:01, 199.70it/s]7) 
405it [00:02, 200.73it/s]7) 
426it [00:02, 200.59it/s]7) 
447it [00:02, 201.41it/s]7) 
469it [00:02, 204.93it/s]7) 
491it [00:02, 207.58it/s]7) 
513it [00:02, 210.34it/s]7) 
535it [00:02, 212.36it/s]7) 
557it [00:02, 213.52it/s]7) 
579it [00:02, 212.39it/s]7) 
601it [00:02, 211.00it/s]7) 
623it [00:03, 208.22it/s]7) 
646it [00:03, 212.05it/s]7) 
670it [00:03, 217.64it/s]7) 
693it [00:03, 220.51it/s]7) 
716it [00:03, 220.67it/s]7) 
739it [00:03, 219.85it/s]7) 
762it [00:03, 

(process pid=9527) SAVING EP, ep-0058, NORMAL-300k


25it [00:00, 246.97it/s]27) 
52it [00:00, 260.11it/s]27) 
80it [00:00, 267.46it/s]27) 
107it [00:00, 246.94it/s]7) 
132it [00:00, 225.57it/s]7) 
155it [00:00, 216.31it/s]7) 
177it [00:00, 212.74it/s]7) 
199it [00:00, 211.06it/s]7) 
221it [00:01, 201.07it/s]7) 
242it [00:01, 193.13it/s]7) 
262it [00:01, 193.57it/s]7) 
282it [00:01, 189.42it/s]7) 
301it [00:01, 188.53it/s]7) 
325it [00:01, 201.28it/s]7) 
346it [00:01, 202.13it/s]7) 
367it [00:01, 197.56it/s]7) 
387it [00:01, 194.30it/s]7) 
407it [00:01, 195.36it/s]7) 
427it [00:02, 195.98it/s]7) 
447it [00:02, 193.71it/s]7) 
467it [00:02, 192.35it/s]7) 
489it [00:02, 199.21it/s]7) 
512it [00:02, 206.15it/s]7) 
535it [00:02, 211.63it/s]7) 
559it [00:02, 217.58it/s]7) 
584it [00:02, 226.74it/s]7) 
614it [00:02, 246.09it/s]7) 
640it [00:02, 247.48it/s]7) 
665it [00:03, 237.82it/s]7) 
689it [00:03, 224.80it/s]7) 
712it [00:03, 215.42it/s]7) 
734it [00:03, 208.20it/s]7) 
755it [00:03, 204.75it/s]7) 
776it [00:03, 201.51it/s]7) 
797it [00:03, 

(process pid=9527) SAVING EP, ep-0059, NORMAL-300k


21it [00:00, 204.55it/s]27) 
45it [00:00, 221.98it/s]27) 
68it [00:00, 214.00it/s]27) 
90it [00:00, 213.90it/s]27) 
116it [00:00, 227.67it/s]7) 
139it [00:00, 217.22it/s]7) 
161it [00:00, 208.83it/s]7) 
188it [00:00, 224.92it/s]7) 
211it [00:00, 225.49it/s]7) 
234it [00:01, 213.33it/s]7) 
256it [00:01, 208.35it/s]7) 
278it [00:01, 209.30it/s]7) 
300it [00:01, 207.66it/s]7) 
321it [00:01, 203.25it/s]7) 
342it [00:01, 203.39it/s]7) 
363it [00:01, 202.06it/s]7) 
389it [00:01, 216.30it/s]7) 
414it [00:01, 225.88it/s]7) 
443it [00:02, 242.40it/s]7) 
468it [00:02, 240.52it/s]7) 
493it [00:02, 238.43it/s]7) 
517it [00:02, 236.00it/s]7) 
546it [00:02, 249.65it/s]7) 
571it [00:02, 249.32it/s]7) 
596it [00:02, 232.63it/s]7) 
620it [00:02, 220.74it/s]7) 
643it [00:02, 212.56it/s]7) 
665it [00:03, 209.27it/s]7) 
687it [00:03, 206.83it/s]7) 
708it [00:03, 203.95it/s]7) 
729it [00:03, 202.98it/s]7) 
750it [00:03, 201.54it/s]7) 
772it [00:03, 205.59it/s]7) 
795it [00:03, 211.98it/s]7) 
817it [00:03, 

In [43]:
import gymu
import jnu as J
dataset = gymu.data.dataset("./NORMAL-300k/ep-0020.tar.gz").then(gymu.data.Composable.decode())
for x in dataset:
    print(x['done'], [(k, v.dtype) for k,v in x.items() if hasattr(v, "dtype")])
    print(x['info'])
    


0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 2.          0.14164704  0.5100001   0.07165179 -0.         48.767544
  0.        ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 2.          0.14164704  0.5100001   0.07165179 -0.         46.96755
  0.        ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 0.          0.14164704  0.5100001   0.07165179 -0.         46.96755
  0.        ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.          0.20012443  0.5100001   0.12624478 -0.         46.96755
  0.        ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('

0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         5.5426154  0.5100001  5.3029356 -0.        46.96756
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         5.601093   0.5100001  5.3575287 -0.        46.96756
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         5.65957    0.5100001  5.412122  -0.        46.96756
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         5.7180476  0.5100001  5.466715  -0.        46.96756
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32'))

0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  2.          7.1116867   0.5100001   7.3256984   0.        297.16757
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  2.          7.1116867   0.5100001   7.3256984   0.        295.36758
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  2.          7.1116867   0.5100001   7.3256984   0.        293.56757
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  2.          7.1116867   0.5100001   7.3256984   0.        291.76758
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')),

0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  2.          3.0101511   0.5100001   7.4732842   0.        255.76753
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  2.          3.0101511   0.5100001   7.4732842   0.        253.96753
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  0.          3.0101511   0.5100001   7.4732842   0.        253.96753
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  2.          3.0101511   0.5100001   7.4732842   0.        252.16754
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')),

0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  1.         -1.6649336   0.5100001   7.498188    0.        270.16748
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  1.         -1.7449332   0.5100001   7.4984217   0.        270.16748
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  1.         -1.8249329   0.5100001   7.4986553   0.        270.16748
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  1.         -1.9049326   0.5100001   7.498889    0.        270.16748
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')),

...

0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  0.          7.48478     0.5100001  -3.9094574   0.        192.76743
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  3.          7.48478     0.5100001  -3.9094574   0.        194.56741
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  3.          7.48478     0.5100001  -3.9094574   0.        196.36742
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  3.          7.48478     0.5100001  -3.9094574   0.        198.16742
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')),

0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  3.          5.3794136   0.5100001  -7.1134353   0.        239.56743
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  3.          5.3794136   0.5100001  -7.1134353   0.        241.36743
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  1.          5.309197    0.5100001  -7.1517706   0.        241.36743
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  0.          5.309197    0.5100001  -7.1517706   0.        241.36743
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')),

0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  3.          3.5175283   0.5100001  -6.9233336   0.        315.16745
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  1.          3.4611254   0.5100001  -6.8666      0.        315.16745
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  1.          3.4047225   0.5100001  -6.8098664   0.        315.16745
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[  1.          3.3483195   0.5100001  -6.753133    0.        315.16745
   0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')),

0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         1.5011625  0.5100001 -3.39277   -0.         3.767436
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 0.         1.5009766  0.5100001 -3.39277   -0.         3.767436
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         1.5012466  0.5100001 -3.312943  -0.         3.767436
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         1.5013006  0.5100001 -3.233116  -0.         3.767436
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float3

0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.          2.7934625   0.5100001   0.62120926 -0.         37.967453
  0.        ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         2.8426795  0.5100001  0.6842781 -0.        37.967453
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         2.8918965  0.5100001  0.7473469 -0.        37.967453
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('float32')), ('reward', dtype('float32'))]
[ 1.         2.9411135  0.5100001  0.8104157 -0.        37.967453
  0.       ]
0 [('action', dtype('int64')), ('done', dtype('uint8')), ('info', dtype('float32')), ('state', dtype('